### Data Collection

In [16]:
import tarfile
import os

def extract_files(filename, extract_path):
    # Check if extraction is necessary
    if os.path.exists(extract_path):
        print(f"Files already extracted in {extract_path}. Skipping extraction.")
        return

    # Check if the file is a tar archive
    if filename.endswith('.tar') or filename.endswith('.tgz'):
        with tarfile.open(filename, 'r:*') as tar:
            tar.extractall(extract_path)
            print(f"Extracted {filename} to {extract_path}")
    else:
        print("File is not a tar or tgz archive.")

if __name__ == '__main__':
    # Extract words.tgz
    extract_files('data/words.tgz', 'data/words')

    # Extract xml.tar
    extract_files('data/xml.tar', 'data/xml')

Files already extracted in data/words. Skipping extraction.
Files already extracted in data/xml. Skipping extraction.


In [17]:
import os
import pandas as pd
import xml.etree.ElementTree as ET

# Directory containing XML files
directory = 'data/xml'

# Initialize an empty list to hold the word data
data = []

# Loop through each file in the directory
for filename in os.listdir(directory):
    if filename.endswith('.xml'):
        # Construct the full file path
        file_path = os.path.join(directory, filename)
        
        # Parse the XML
        tree = ET.parse(file_path)
        root = tree.getroot()
        
        # Extract word data
        for word in root.findall('.//word'):
            word_id = word.get('id')
            text = word.get('text')
            tag = word.get('tag')
            components = [(int(cmp.get('x')), int(cmp.get('y')), int(cmp.get('width')), int(cmp.get('height'))) for cmp in word.findall('.//cmp')]
            
            # Append the data to our list
            data.append([word_id, text, tag, components])

# Create a DataFrame from the list
df = pd.DataFrame(data, columns=['WordID', 'Text', 'Tag', 'Components'])


In [19]:
df

WordID         Text   Tag  \
0        d06-050-00-00          Nor    CC   
1        d06-050-00-01           is   BEZ   
2        d06-050-00-02          she  PP3A   
3        d06-050-00-03  necessarily    RB   
4        d06-050-00-04        being   BEG   
...                ...          ...   ...   
115315  g06-018m-07-06           of   INO   
115316  g06-018m-07-07            a    AT   
115317  g06-018m-07-08         fire    NN   
115318  g06-018m-07-09          ...   ...   
115319  g06-018m-07-10            .     .   

                                               Components  
0                [(354, 752, 43, 67), (399, 773, 50, 36)]  
1                 [(495, 780, 7, 35), (502, 766, 14, 51)]  
2                [(553, 776, 33, 33), (588, 741, 54, 68)]  
3       [(697, 771, 50, 39), (759, 764, 82, 44), (849,...  
4       [(1027, 750, 64, 62), (1093, 781, 21, 26), (10...  
...                                                   ...  
115315                             [(1364, 1923, 72, 70)]  
115316                             [(1451, 1956, 35, 29)]  
115317       [(1541, 1916, 142, 88), (1623, 1924, 11, 7)]  
115318          [(1712, 1978, 6, 8), (1734, 1978, 7, 10)]  
115319                                                 []  

[115320 rows x 4 columns]

In [ ]:
import cv2
import numpy as np

def load_and_preprocess_image(image_path, components, target_size=(64, 64)):
    # Load the image in grayscale
    image = cv2.imread(image_path, cv2.IMREAD_GRAYSCALE)
    
    # Initialize a list to hold the processed components
    processed_components = []
    
    for (x, y, width, height) in components:
        # Crop the image to the component's bounding box
        cropped = image[y:y+height, x:x+width]
        
        # Resize the image to the target size
        resized = cv2.resize(cropped, target_size)
        
        # Normalize pixel values to be between 0 and 1
        normalized = resized / 255.0
        
        # Append the processed image to the list
        processed_components.append(normalized)
    
    # Combine the processed components into one array (if necessary)
    # Depending on your model, you might concatenate, stack, or average them
    # For simplicity, we'll stack them here
    combined = np.stack(processed_components, axis=0)
    
    return combined

In [25]:
import pandas as pd

# Path to your text file
file_path = 'data/words.txt'

# Initialize an empty list to hold the parsed data
data = []

# Open and read the file line by line
with open(file_path, 'r') as file:
    for line in file:
        # Skip lines that don't contain the data (like comments)
        if line.startswith('#') or not line.strip():
            continue

        # Split the line into parts
        parts = line.split()

        # Extract the relevant information
        word_id = parts[0]
        segmentation_result = parts[1]
        graylevel = int(parts[2])
        #num_components = int(parts[3])
        bounding_box = tuple(map(int, parts[3:7]))
        grammatical_tag = parts[7]
        transcription = ' '.join(parts[8:])

        # Append the data to the list
        data.append([word_id, segmentation_result, graylevel, bounding_box, grammatical_tag, transcription])

# Create a DataFrame from the list
df = pd.DataFrame(data, columns=['WordID', 'SegmentationResult', 'GrayLevel', 'BoundingBox', 'GrammaticalTag', 'Transcription'])

# Display the first few rows of the DataFrame
df.head()


WordID SegmentationResult  GrayLevel           BoundingBox  \
0  a01-000u-00-00                 ok        154    (408, 768, 27, 51)   
1  a01-000u-00-01                 ok        154   (507, 766, 213, 48)   
2  a01-000u-00-02                 ok        154    (796, 764, 70, 50)   
3  a01-000u-00-03                 ok        154   (919, 757, 166, 78)   
4  a01-000u-00-04                 ok        154  (1185, 754, 126, 61)   

  GrammaticalTag Transcription  
0             AT             A  
1             NN          MOVE  
2             TO            to  
3             VB          stop  
4            NPT           Mr.

In [28]:
import cv2
import numpy as np
import pandas as pd
from pathlib import Path

def load_image(file_path):
    # Load an image in grayscale mode
    return cv2.imread(str(file_path), cv2.IMREAD_GRAYSCALE)

def preprocess_image(image, target_size=(128, 32)):
    # Resize the image to the target size
    image = cv2.resize(image, target_size, interpolation=cv2.INTER_LINEAR)
    
    # Normalize the image
    image = image.astype(np.float32) / 255.0
    
    # Add a channel dimension ([height, width] -> [height, width, 1])
    image = np.expand_dims(image, axis=-1)
    
    return image


In [34]:
from IPython.display import clear_output
import time

# Assuming you have a DataFrame named df with a 'WordID' column
df['ImageData'] = None  # Prepare a column for the image data

# Define the base directory where the word images are stored
base_dir = Path('data/words')

count = 0
start_time = time.time()
# Loop through all the subdirectories and files in the base directory
for subdir, _, files in os.walk(base_dir):
    for file_name in files:
        if file_name.endswith('.png'):
            # Extract the WordID from the file name (assuming it matches the WordID format)
            word_id = file_name[:-4]  # Remove the '.png' extension
            
            # Check if this WordID is in the DataFrame
            if word_id in df['WordID'].values:
                img_path = Path(subdir) / file_name
                
                try:
                    # Load and preprocess the image
                    img = load_image(img_path)
                    img = preprocess_image(img)
                    
                    # Find the index in the DataFrame where this WordID is located
                    idx = df.index[df['WordID'] == word_id].tolist()[0]
                    
                    # Assign the preprocessed image to the correct row in the DataFrame
                    df.at[idx, 'ImageData'] = img

                    count += 1
                    print(f"Processed {count} images.", end='\r')
                    clear_output(wait=True)
                    
                except Exception as e:
                    print(f"Error processing {img_path}: {e}")

    if count >= 1000:
        print("elapsed time (seconds):", time.time() - start_time)
        print(f"Processed {count} images.", end='\r')
        break


elapsed time (seconds): 11.660638809204102


In [37]:
images = df[~df['ImageData'].isnull()]

In [49]:
import matplotlib.pyplot as plt
import numpy as np

def display_images(dataframe, num_images=100):
    # Calculate the number of rows and columns (you might want to tweak these values)
    cols = 5  # for example, 10 images per row
    rows = int(np.ceil(num_images / cols))

    fig, axes = plt.subplots(rows, cols, figsize=(20, 2 * rows))  # Adjust the size as needed

    for i in range(num_images):
        if i >= len(dataframe):
            break  # Break if there are no more images to display

        # Convert 1D array of axes to 2D for easier indexing
        ax = axes[i // cols, i % cols] if rows > 1 else axes[i]

        # Get the image data from the DataFrame
        img_data = dataframe.iloc[i]['ImageData']
        
        if img_data is not None:
            img = np.squeeze(img_data)
            ax.imshow(img, cmap='gray')
            ax.set_title(f"text: {dataframe.iloc[i]['Transcription']}, id: {dataframe.iloc[i]['WordID']}", fontsize=6)
        else:
            ax.set_title("No image data", fontsize=6)

        ax.axis('off')  # Turn off axis numbers and ticks

    # Hide any unused subplots
    for i in range(num_images, rows * cols):
        axes.flatten()[i].axis('off')

    plt.tight_layout()
    plt.show()

# Call the function with your DataFrame
display_images(images, num_images=30)  # Adjust num_images as needed

Image paths txt

In [52]:
import os
from pathlib import Path

def export_image_paths(base_dir, output_file):
    base_path = Path(base_dir)
    with open(output_file, 'w') as file:
        # Walk through the directory
        for subdir, _, files in os.walk(base_path):
            for filename in files:
                # Check if the file is a .png
                if filename.endswith('.png'):
                    # Construct the full path
                    full_path = Path(subdir) / filename
                    # Write the path to the file
                    file.write(str(full_path) + '\n')

# Set your base directory and output file name
base_directory = 'data/words'
output_txt_file = 'data/img_paths.txt'

# Call the function with your specified paths
export_image_paths(base_directory, output_txt_file)

In [58]:
import matplotlib.pyplot as plt
import numpy as np
import cv2
from pathlib import Path

def load_original_image(file_path):
    return cv2.imread(str(file_path), cv2.IMREAD_GRAYSCALE)

def read_image_paths(file_path):
    with open(file_path, 'r') as file:
        return {Path(line.strip()).stem: line.strip() for line in file}

def display_images_side_by_side(dataframe, img_paths_file='img_paths.txt', num_pairs=10):
    # Load image paths from the file
    img_paths = read_image_paths(img_paths_file)
    
    # Calculate rows needed (one row per pair)
    rows = num_pairs

    fig, axes = plt.subplots(rows, 2, figsize=(10, 2 * rows))  # 2 columns for original and processed

    for i in range(num_pairs):
        if i >= len(dataframe):
            break  # Break if there are no more images to display

        word_id = dataframe.iloc[i]['WordID']
        text = dataframe.iloc[i]['Transcription']

        # Use the path from the img_paths dictionary
        original_img_path = img_paths.get(word_id)

        # Define axes for original and processed images
        ax_original = axes[i, 0] if rows > 1 else axes[0]
        ax_processed = axes[i, 1] if rows > 1 else axes[1]

        # Show original image
        if original_img_path:
            original_img = load_original_image(original_img_path)
            if original_img is not None:
                ax_original.imshow(original_img, cmap='gray')
                ax_original.set_title(f"Original: {text}", fontsize=8)
            else:
                ax_original.set_title("Original image not found", fontsize=8)
        else:
            ax_original.set_title("Path not found in img_paths.txt", fontsize=8)
        ax_original.axis('off')

        # Show processed image
        processed_img_data = dataframe.iloc[i]['ImageData']
        if processed_img_data is not None:
            processed_img = np.squeeze(processed_img_data)
            ax_processed.imshow(processed_img, cmap='gray')
            ax_processed.set_title(f"Processed: {text}", fontsize=8)
        else:
            ax_processed.set_title("Processed image data not available", fontsize=8)
        ax_processed.axis('off')

    plt.tight_layout()
    plt.show()

# Call the function with your DataFrame and the text file containing image paths
display_images_side_by_side(images, img_paths_file='data/img_paths.txt', num_pairs=100)  # Adjust num_pairs as needed